# Individual Assignment

### Table of Contents

[Dataset](#Dataset)

[Data Preparation](#Data-Preparation)

[Inserting Data Into SQL](#Inserting-Data-Into-SQL)

[Guiding Question #1: Total Crime Count by Category](#Guiding-Question-#1:-Total-Crime-Count-by-Category)

[Guiding Question #2: Total Crime Count by Community](#Guiding-Question-#2:-Total-Crime-Count-by-Community)

[Guiding Question #3: Types of Crime by Community](#Guiding-Question-#3:-Types-of-Crime-by-Community)

[Guiding Question #4: Monthly Crime Trends](#Guiding-Question-#4:-Monthly-Crime-Trends)

[Guiding Question #5: Total Crime Count by Sector](#Guiding-Question-#5:-Total-Crime-Count-by-Sector)

[References](#References)

## Dataset

This dataset is from the Calgary Open Database. The data is provided monthly by the Calgary Police Service. The data used for this project is a subset of the original dataset, since our project looks at census data from 2019, the subset of the data that is used in this project is only the data from 2019. 

Here is a link to the original data, before being filtered to just data from 2019:

https://data.calgary.ca/Health-and-Safety/Community-Crime-Statistics/78gh-n26t


## Data Preparation

This section reads the csv and does some data cleaning so that it can be added to the MariaDB

In [9]:
import pandas as pd
import numpy as np

crimestats = pd.read_csv("https://raw.githubusercontent.com/ethan2411/Data-603-604/main/604%20Data/Community_Crime_Statistics.csv")
crimestats.head(5)

Sector Community Name                    Category  Crime Count     Date  \
0    NaN            14V  Break & Enter - Commercial            1  2019/04   
1    NaN            02A      Assault (Non-domestic)            1  2019/12   
2    NaN            10A          Theft FROM Vehicle            1  2019/01   
3    NaN            10C            Theft OF Vehicle            1  2019/11   
4    NaN            14V          Theft FROM Vehicle            1  2019/01   

   Year Month                                       ID  Resident Count  \
0  2019   APR  2019-APR-14V-Break & Enter - Commercial             NaN   
1  2019   DEC      2019-DEC-02A-Assault (Non-domestic)             NaN   
2  2019   JAN          2019-JAN-10A-Theft FROM Vehicle             NaN   
3  2019   NOV            2019-NOV-10C-Theft OF Vehicle             NaN   
4  2019   JAN          2019-JAN-14V-Theft FROM Vehicle             NaN   

  Community Center Point  Calgary Communities  Ward Boundaries 2013-2017  \
0                    NaN                  NaN                        NaN   
1                    NaN                  NaN                        NaN   
2                    NaN                  NaN                        NaN   
3                    NaN                  NaN                        NaN   
4                    NaN                  NaN                        NaN   

   Ward Boundaries  City Quadrants  
0              NaN             NaN  
1              NaN             NaN  
2              NaN             NaN  
3              NaN             NaN  
4              NaN             NaN

In [10]:
df1 = crimestats.drop('Resident Count', axis=1)
df1.columns = ["Sector", "CommunityName","Category","CrimeCount","Date", "Year", "Month", "ID","CommunityCenterPoint","CalgaryCommunities","WardBoundaries20132017", "WardBoundaries", "CityQuadrants"]

Some initial data wrangling and cleaning was conducted before inserting the data. All NaN values were removed since MariaDB only accepts null values which are not NaN so we were getting errors when trying to inserrt data will NaN values so in the end we decided to remove all missing values before hand

In [11]:
df1.dropna(inplace=True)
df1.head(5)

Sector CommunityName                Category  CrimeCount     Date  Year  \
8    WEST           01C      Theft FROM Vehicle           1  2019/08  2019   
10  SOUTH      PARKLAND        Theft OF Vehicle           1  2019/01  2019   
11  SOUTH      SOMERSET          Street Robbery           1  2019/02  2019   
12   WEST      LAKEVIEW        Theft OF Vehicle           1  2019/11  2019   
13  NORTH      STONEY 1  Assault (Non-domestic)           1  2019/09  2019   

   Month                                        ID  \
8    AUG           2019-AUG-01C-Theft FROM Vehicle   
10   JAN        2019-JAN-PARKLAND-Theft OF Vehicle   
11   FEB          2019-FEB-SOMERSET-Street Robbery   
12   NOV        2019-NOV-LAKEVIEW-Theft OF Vehicle   
13   SEP  2019-SEP-STONEY 1-Assault (Non-domestic)   

                CommunityCenterPoint  CalgaryCommunities  \
8   POINT (-114.2380197 51.08500322)               291.0   
10   POINT (-114.0285394 50.9211972)               117.0   
11  POINT (-114.0813075 50.89869686)                55.0   
12  POINT (-114.1296334 50.99977294)               129.0   
13  POINT (-114.0246985 51.16118788)               163.0   

    WardBoundaries20132017  WardBoundaries  CityQuadrants  
8                      9.0            13.0            1.0  
10                    13.0             6.0            3.0  
11                     6.0             5.0            1.0  
12                     5.0             8.0            1.0  
13                    12.0            11.0            4.0

In [12]:
#print the sum of NaN values in each column, will have to deal with those
print(len(crimestats))
print(df1.isna().sum())

11857
Sector                    0
CommunityName             0
Category                  0
CrimeCount                0
Date                      0
Year                      0
Month                     0
ID                        0
CommunityCenterPoint      0
CalgaryCommunities        0
WardBoundaries20132017    0
WardBoundaries            0
CityQuadrants             0
dtype: int64


## Inserting Data Into SQL

Creating the database and inserting the data into it

### Connecting to database

In [13]:
#in cmd do mysql.connector or mysql-connector-python
import mysql.connector
from mysql.connector import errorcode

filepath = "C:/Users/ethan/Downloads/Data 604/Term Project/password.txt"

with open(filepath) as f:
    passw = f.read()
    
# attempt a connection
myconnection = mysql.connector.connect(user='ethan_scott', 
                                       password=passw,
                                       host='datasciencedb2.ucalgary.ca', 
                                       database='ethan_scott',
                                       allow_local_infile=True)
myconnection

### Creating table in SQL

In [7]:
# CREATE TABLE STATEMENT
create_statement = '''create table ethan_scott.crimestats (
    Sector varchar(10),
    CommunityName varchar(250) NOT NULL,
    Category varchar(40),
    CrimeCount int,
    Date varchar(7),
    Year varchar(4),
    Month varchar(3),
    ID varchar(100),
    CommunityCenterPoint blob,
    CalgaryCommunities int,
    WardBoundaries20132017 int,
    WardBoundaries int,
    CityQuadrants int
    );'''

# now we'll create a cursor and run our create statement
create_cursor = myconnection.cursor()
try:
    create_cursor.execute(create_statement)
except mysql.connector.Error as err:
    if err.errno == errorcode.ER_TABLE_EXISTS_ERROR:
        print("Ooops! We already have that table")
    else:
        print(err.msg)
else:
    print("table created successfully!")

create_cursor.close()

Ooops! We already have that table


True

### Insert data into SQL

In [8]:
insertCursor = myconnection.cursor()

columnString = "`,`".join([str(currentColumn) for currentColumn in df1.columns.tolist()])
#print (columnString)

# inserting rows one by one from the DataFrame is sufficient for now
for i, currentRow in df1.iterrows():
    #print (tuple(currentRow))
    insertCommand = "INSERT INTO `crimestats` (`" + columnString + "`) VALUES (" + "%s,"*(len(currentRow)-1) + "%s)"
    insertCursor.execute(insertCommand, tuple(currentRow))
    
myconnection.commit()

insertCursor.close()

KeyboardInterrupt: 

In [14]:
# Seeing all the data
read_cursor = myconnection.cursor(buffered=True, dictionary=True)

query_string = ("SELECT * FROM crimestats;")

read_cursor.execute(query_string)

for (library_value) in read_cursor:
    print(library_value)
    
read_cursor.close()

{'Sector': 'WEST', 'CommunityName': '01C', 'Category': 'Theft FROM Vehicle', 'CrimeCount': 1, 'Date': '2019/08', 'Year': '2019', 'Month': 'AUG', 'ID': '2019-AUG-01C-Theft FROM Vehicle', 'CommunityCenterPoint': b'POINT (-114.2380197 51.08500322)', 'CalgaryCommunities': 291, 'WardBoundaries20132017': 9, 'WardBoundaries': 13, 'CityQuadrants': 1}
{'Sector': 'SOUTH', 'CommunityName': 'PARKLAND', 'Category': 'Theft OF Vehicle', 'CrimeCount': 1, 'Date': '2019/01', 'Year': '2019', 'Month': 'JAN', 'ID': '2019-JAN-PARKLAND-Theft OF Vehicle', 'CommunityCenterPoint': b'POINT (-114.0285394 50.9211972)', 'CalgaryCommunities': 117, 'WardBoundaries20132017': 13, 'WardBoundaries': 6, 'CityQuadrants': 3}
{'Sector': 'SOUTH', 'CommunityName': 'SOMERSET', 'Category': 'Street Robbery', 'CrimeCount': 1, 'Date': '2019/02', 'Year': '2019', 'Month': 'FEB', 'ID': '2019-FEB-SOMERSET-Street Robbery', 'CommunityCenterPoint': b'POINT (-114.0813075 50.89869686)', 'CalgaryCommunities': 55, 'WardBoundaries20132017': 6,

True

## Guiding Question #1: Total Crime Count by Category

The query is valuable for gaining insights into the distribution and prevalence of different crime categories within the dataset. By calculating the total count of each crime category using the SUM(CrimeCount) aggregation, the query helps to identify which types of crimes are more prevalent overall. 

This will allow for us to have a deeper understanding of the distributon of crimes in valgary and will help when exploring the relationship between the types of crimes and the other datasets we are using for our project.

In [15]:
# Amount of each crime
read_cursor = myconnection.cursor(buffered=True, dictionary=True)

query_string = ("SELECT Category, SUM(CrimeCount) AS TotalCrimeCount FROM crimestats GROUP BY Category ORDER BY TotalCrimeCount DESC;")

read_cursor.execute(query_string)

for (library_value) in read_cursor:
    print(library_value)
    
read_cursor.close()

{'Category': 'Theft FROM Vehicle', 'TotalCrimeCount': Decimal('14658')}
{'Category': 'Theft OF Vehicle', 'TotalCrimeCount': Decimal('6009')}
{'Category': 'Break & Enter - Commercial', 'TotalCrimeCount': Decimal('5767')}
{'Category': 'Assault (Non-domestic)', 'TotalCrimeCount': Decimal('3909')}
{'Category': 'Break & Enter - Dwelling', 'TotalCrimeCount': Decimal('2391')}
{'Category': 'Break & Enter - Other Premises', 'TotalCrimeCount': Decimal('2294')}
{'Category': 'Violence Other (Non-domestic)', 'TotalCrimeCount': Decimal('1871')}
{'Category': 'Street Robbery', 'TotalCrimeCount': Decimal('642')}
{'Category': 'Commercial Robbery', 'TotalCrimeCount': Decimal('384')}


True

## Guiding Question #2: Total Crime Count by Community

This query is crucial for obtaining a comprehensive understanding of the crime distribution across different communities in Calgary. Through the SUM(CrimeCount) aggregation, the query calculates the total crime count for each community, allowing for the identification of areas with higher overall crime rates.

Moreover, the query's results provide a valuable foundation for exploring the relationship between crime types and other datasets in the project. By knowing the total crime counts in each community we can compare these results with the other datasets.

In [16]:
#Total Crime by community
read_cursor = myconnection.cursor(buffered=True, dictionary=True)

query_string = ("SELECT CommunityName, SUM(CrimeCount) as TotalCrime FROM crimestats GROUP BY CommunityName ORDER BY TotalCrime DESC;")

read_cursor.execute(query_string)

for (library_value) in read_cursor:
    print(library_value)
    
read_cursor.close()

{'CommunityName': 'BELTLINE', 'TotalCrime': Decimal('2270')}
{'CommunityName': 'DOWNTOWN COMMERCIAL CORE', 'TotalCrime': Decimal('1642')}
{'CommunityName': 'FOREST LAWN', 'TotalCrime': Decimal('529')}
{'CommunityName': 'HILLHURST', 'TotalCrime': Decimal('460')}
{'CommunityName': 'MANCHESTER INDUSTRIAL', 'TotalCrime': Decimal('456')}
{'CommunityName': 'ACADIA', 'TotalCrime': Decimal('418')}
{'CommunityName': 'BOWNESS', 'TotalCrime': Decimal('408')}
{'CommunityName': 'CRESCENT HEIGHTS', 'TotalCrime': Decimal('396')}
{'CommunityName': 'SUNRIDGE', 'TotalCrime': Decimal('369')}
{'CommunityName': 'FALCONRIDGE', 'TotalCrime': Decimal('367')}
{'CommunityName': 'ALBERT PARK/RADISSON HEIGHTS', 'TotalCrime': Decimal('366')}
{'CommunityName': 'RUNDLE', 'TotalCrime': Decimal('357')}
{'CommunityName': 'TEMPLE', 'TotalCrime': Decimal('356')}
{'CommunityName': 'DOVER', 'TotalCrime': Decimal('354')}
{'CommunityName': 'BRIDGELAND/RIVERSIDE', 'TotalCrime': Decimal('354')}
{'CommunityName': 'HUNTINGTON HI

True

## Guiding Question #3: Types of Crime by Community

The presented query is pivotal for examining the distribution of different crime categories across various communities within the dataset. By utilizing the SUM(CrimeCount) aggregation and grouping the results by both community name and crime category, the query allows for a granular analysis of the prevalence of specific crimes in each sector.

Furthermore, the query's output lays the groundwork for a more nuanced exploration of the relationships between crime types, community characteristics, and sector-specific factors. Investigating the total crime counts for each combination of community and category enhances the analytical depth, facilitating a more comprehensive understanding of crime patterns within specific sectors.

In [17]:
# Amount of each crime per sector
read_cursor = myconnection.cursor(buffered=True, dictionary=True)

query_string = ("SELECT CommunityName, Category, SUM(CrimeCount) as TotalCrime FROM crimestats GROUP BY CommunityName, Category ORDER BY TotalCrime DESC;;")

read_cursor.execute(query_string)

for (library_value) in read_cursor:
    print(library_value)
    
read_cursor.close()

{'CommunityName': 'BELTLINE', 'Category': 'Theft FROM Vehicle', 'TotalCrime': Decimal('912')}
{'CommunityName': 'DOWNTOWN COMMERCIAL CORE', 'Category': 'Theft FROM Vehicle', 'TotalCrime': Decimal('730')}
{'CommunityName': 'BELTLINE', 'Category': 'Break & Enter - Commercial', 'TotalCrime': Decimal('601')}
{'CommunityName': 'BELTLINE', 'Category': 'Assault (Non-domestic)', 'TotalCrime': Decimal('378')}
{'CommunityName': 'DOWNTOWN COMMERCIAL CORE', 'Category': 'Assault (Non-domestic)', 'TotalCrime': Decimal('361')}
{'CommunityName': 'DOWNTOWN COMMERCIAL CORE', 'Category': 'Break & Enter - Commercial', 'TotalCrime': Decimal('310')}
{'CommunityName': 'HILLHURST', 'Category': 'Theft FROM Vehicle', 'TotalCrime': Decimal('209')}
{'CommunityName': 'ACADIA', 'Category': 'Theft FROM Vehicle', 'TotalCrime': Decimal('197')}
{'CommunityName': 'MISSION', 'Category': 'Theft FROM Vehicle', 'TotalCrime': Decimal('170')}
{'CommunityName': 'MANCHESTER INDUSTRIAL', 'Category': 'Theft FROM Vehicle', 'TotalC

True

## Guiding Question #4: Monthly Crime Trends

he provided query is essential for unraveling the patterns of crime occurrences within the dataset. By leveraging the SUM(CrimeCount) aggregation and grouping the results by month, the query yields valuable insights into the variations of total crime counts over different months. This information is crucial for identifying potential seasonal trends, patterns, or fluctuations in criminal activities

Moreover, the query's output serves as a foundational element for exploring the dynamics of crime in more detail. Analyzing total crime counts on a monthly basis provides a basis for identifying specific periods of heightened or reduced criminal activities.

In [18]:
# Amount of each crime per month
read_cursor = myconnection.cursor(buffered=True, dictionary=True)

query_string = ("SELECT SUBSTR(Date, 6, 2) AS Month, SUM(CrimeCount) AS TotalCrimeCount FROM crimestats GROUP BY Month ORDER BY TotalCrimeCount DESC;")

read_cursor.execute(query_string)

for (library_value) in read_cursor:
    print(library_value)
    
read_cursor.close()

{'Month': '09', 'TotalCrimeCount': Decimal('3858')}
{'Month': '08', 'TotalCrimeCount': Decimal('3779')}
{'Month': '07', 'TotalCrimeCount': Decimal('3749')}
{'Month': '10', 'TotalCrimeCount': Decimal('3354')}
{'Month': '06', 'TotalCrimeCount': Decimal('3332')}
{'Month': '05', 'TotalCrimeCount': Decimal('3146')}
{'Month': '11', 'TotalCrimeCount': Decimal('3077')}
{'Month': '01', 'TotalCrimeCount': Decimal('3046')}
{'Month': '04', 'TotalCrimeCount': Decimal('2803')}
{'Month': '12', 'TotalCrimeCount': Decimal('2785')}
{'Month': '03', 'TotalCrimeCount': Decimal('2684')}
{'Month': '02', 'TotalCrimeCount': Decimal('2312')}


True

## Guiding Question #5: Total Crime Count by Sector

The presented query plays a crucial role in examining the distribution of crime across different sectors within the dataset. By utilizing the SUM(CrimeCount) aggregation and grouping the results by sector, the query provides valuable insights into the overall crime landscape in each sector of Calgary.

Furthermore, the query's output serves as a foundational element for exploring the relationship between crime patterns and sector-specific characteristics. Analyzing total crime counts by sector contributes to a nuanced understanding of the unique dynamics influencing criminal activities in different areas.

In [19]:
#crime in each sector, could also do community
read_cursor = myconnection.cursor(buffered=True, dictionary=True)

query_string = ("SELECT Sector, SUM(CrimeCount) AS TotalCrimeCount FROM crimestats GROUP BY Sector;")

read_cursor.execute(query_string)

for (library_value) in read_cursor:
    print(library_value)
    
read_cursor.close()

{'Sector': 'CENTRE', 'TotalCrimeCount': Decimal('13478')}
{'Sector': 'EAST', 'TotalCrimeCount': Decimal('2928')}
{'Sector': 'NORTH', 'TotalCrimeCount': Decimal('2499')}
{'Sector': 'NORTHEAST', 'TotalCrimeCount': Decimal('6481')}
{'Sector': 'NORTHWEST', 'TotalCrimeCount': Decimal('3073')}
{'Sector': 'SOUTH', 'TotalCrimeCount': Decimal('4912')}
{'Sector': 'SOUTHEAST', 'TotalCrimeCount': Decimal('2241')}
{'Sector': 'WEST', 'TotalCrimeCount': Decimal('2313')}


True

In [ ]:
#Closing connection
myconnection.close()

## References

Community crime statistics | open calgary. (n.d.). Retrieved October 28, 2023, from https://data.calgary.ca/Health-and-Safety/Community-Crime-Statistics/78gh-n26t
